In [1]:
# Import Splinter and BeautifulSoup
from splinter import Browser
from bs4 import BeautifulSoup as soup
from webdriver_manager.chrome import ChromeDriverManager
from selenium import webdriver
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.common.by import By
from selenium.common.exceptions import TimeoutException, NoSuchElementException
import time
import pandas as pd

In [2]:
executable_path = {'executable_path': ChromeDriverManager().install()}
browser = Browser('chrome', **executable_path, headless=False)



====== WebDriver manager ======
Current google-chrome version is 101.0.4951
Get LATEST chromedriver version for 101.0.4951 google-chrome
Trying to download new driver from https://chromedriver.storage.googleapis.com/101.0.4951.41/chromedriver_win32.zip
Driver has been saved in cache [C:\Users\drewa\.wdm\drivers\chromedriver\win32\101.0.4951.41]


## Cancer Incidence Data

In [3]:
# Visit the State Cancer Profile(Incidence) site
url = 'https://www.statecancerprofiles.cancer.gov/deathrates/index.php'
browser.visit(url)
# Optional delay for loading the page
browser.is_element_present_by_css('div.col-xs-9', wait_time=1)

True

In [4]:
# Set the html parameter of interest
html = browser.html
can_soup = soup(html, 'html.parser')
slide_elem = can_soup.select_one('fieldset')

In [5]:
print(slide_elem.prettify())

<fieldset>
 <legend>
  Data Options
 </legend>
 <div class="inputWrap cf">
  <label for="stateFIPS">
   <strong>
    Area:
   </strong>
  </label>
  <select id="stateFIPS" name="stateFIPS" onchange="updateAreaType();">
   <option selected="selected" value="*">
    --- choose state ---
   </option>
   <option value="00">
    United States
   </option>
   <option value="01">
    Alabama
   </option>
   <option value="02">
    Alaska
   </option>
   <option value="04">
    Arizona
   </option>
   <option value="05">
    Arkansas
   </option>
   <option value="06">
    California
   </option>
   <option value="08">
    Colorado
   </option>
   <option value="09">
    Connecticut
   </option>
   <option value="10">
    Delaware
   </option>
   <option value="11">
    District of Columbia
   </option>
   <option value="12">
    Florida
   </option>
   <option value="13">
    Georgia
   </option>
   <option value="15">
    Hawaii
   </option>
   <option value="16">
    Idaho
   </option>
   <

In [6]:
slide_elem.find_all('option')

[<option selected="selected" value="*">--- choose state ---</option>,
 <option value="00">United States</option>,
 <option value="01">Alabama</option>,
 <option value="02">Alaska </option>,
 <option value="04">Arizona</option>,
 <option value="05">Arkansas</option>,
 <option value="06">California</option>,
 <option value="08">Colorado</option>,
 <option value="09">Connecticut</option>,
 <option value="10">Delaware</option>,
 <option value="11">District of Columbia</option>,
 <option value="12">Florida</option>,
 <option value="13">Georgia</option>,
 <option value="15">Hawaii </option>,
 <option value="16">Idaho</option>,
 <option value="17">Illinois</option>,
 <option value="18">Indiana</option>,
 <option value="19">Iowa </option>,
 <option value="20">Kansas </option>,
 <option value="21">Kentucky</option>,
 <option value="22">Louisiana </option>,
 <option value="23">Maine</option>,
 <option value="24">Maryland</option>,
 <option value="25">Massachusetts</option>,
 <option value="26">M

In [7]:
slide_elem.find_all('option')[95:99]

[<option value="009">&lt;50</option>,
 <option value="136">50+</option>,
 <option value="006">&lt;65</option>,
 <option value="157">65+</option>]

In [8]:
# Cancer Incidence Data(2015-2019)

# Data options lists
#Area
state = {}
results = slide_elem.find_all('option')[2:54]
for result in results:
    state[result.attrs['value']] = result.text
state_keys = list(state)
# Cancer
cancer = {}
results = slide_elem.find_all('option')[59:80]
for result in results:
    cancer[result.attrs['value']] = result.text
cancer_keys = list(cancer)
# Race/Ethnicity
race = {}
results = slide_elem.find_all('option')[82:89]
for result in results:
    race[result.attrs['value']] = result.text
race_keys = list(race)
# Sex
sex = {}
results = slide_elem.find_all('option')[91:93]
for result in results:
    sex[result.attrs['value']] = result.text
sex_keys = list(sex)
# Age
age = {}
results = slide_elem.find_all('option')[95:99]
for result in results:
    age[result.attrs['value']] = result.text
age_keys = list(age)


In [9]:
# Reset dictionaries
cancer_reset = {'001':'All Cancer Sites'}
race_reset = {'00':'All Races (includes Hispanic)'}
sex_reset = {'0':'Both Sexes'}
age_reset = {'001':'All Ages'}

In [10]:
# site = f'https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS={state_num}&areatype=county&cancer={cancer_num}&race={race_num}&sex={sex_num}&age={age_num}&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results'

# For loop to change all data options to relevant data points

# Create empty dataframe
df = []

# Set initial parameters
cancer_num = list(cancer_reset.keys())[0]
race_num = list(race_reset.keys())[0]
sex_num = list(sex_reset.keys())[0]
age_num = list(age_reset.keys())[0]
print(cancer_num, race_num, sex_num, age_num)

001 00 0 001


In [11]:
age_mort_list = []
# Select Age features
cancer_num = list(cancer_reset.keys())[0]
race_num = list(race_reset.keys())[0]
sex_num = list(sex_reset.keys())[0]
age_num = list(age_reset.keys())[0]
for a in range(len(state_keys)):
    state_num = state_keys[a]
    for e in range(len(age_keys)):
        # URL variable
        age_num = age_keys[e]
        # Visit site
        url_to_visit = f'https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS={state_num}'
        url_to_visit += f'&areatype=county&cancer={cancer_num}'
        url_to_visit += f'&race={race_num}&sex={sex_num}'
        url_to_visit += f'&age={age_num}'
        url_to_visit += f'&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results'
        print("cancer_num", url_to_visit)
        
        browser.visit(url_to_visit)
        # Wait for load
        browser.is_element_present_by_css('div.col-xs-9', wait_time=4)
        url2 = f'https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS={state_num}'
        url2 += f'&areatype=county&cancer={cancer_num}'
        url2 += f'&race={race_num}&sex={sex_num}'
        url2 += f'&age={age_num}'
        url2 += f'&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results'
        print("url2", url2)
        y = pd.read_html(url2)[0]
        # Add selection criteria to y
        y.reindex(columns = y.columns.tolist() + ["State", "Cancer", "Race/Ethnicity", "Sex", "Age"])
        y['State'] = state[state_keys[a]]
        y['Cancer'] = "All Cancer Sites"
        y['Race/Ethnicity'] = "All Races (includes Hispanic)"
        y['Sex'] = "All Sexes"
        y['Age'] = age[age_keys[e]]
        # Add to current dataframe
        display(y)
        age_mort_list.append(y)
        # Reset conditionals
        cancer_num = list(cancer_reset.keys())[0]
        race_num = list(race_reset.keys())[0]
        sex_num = list(sex_reset.keys())[0]
        age_num = list(age_reset.keys())[0]
browser.quit()

cancer_num https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=0&age=009&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=0&age=009&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0             Alabama                                  ***   
1       United States                                  ***   
2      Marengo County                                  ***   
3      Jackson County                                  ***   
4     Randolph County                                  ***   
..                ...                                  ...   
64     Pickens County                                  ***   
65      Sumter County                                  ***   
66  Washington County                                  ***   
67      Wilcox County                                  ***   
68     Winston County                                  ***   

   Age-Adjusted Death Rate†deaths per 100,000(95% Confidence Interval)  \
0                                   18.4 (17.7, 19.1)                    
1                                   15.1 (15.1, 15.2)                    
2                                   38.8 (24.2, 58.8)                    
3                                   30.2 (22.0, 40.3)                    
4                                   27.6 (16.0, 44.2)                    
..                                                ...                    
64                                                  *                    
65                                                  *                    
66                                                  *                    
67                                                  *                    
68                                                  *                    

   CI*Rank&fork;(95% Confidence Interval) Average Annual Count Recent Trend  \
0                                     NaN                  543      falling   
1                                     NaN                30333      falling   
2                               1 (1, 30)                    4            *   
3                               2 (1, 28)                    9       stable   
4                               3 (1, 41)                    3       stable   
..                                    ...                  ...          ...   
64                                      *           3 or fewer            *   
65                                      *           3 or fewer            *   
66                                      *           3 or fewer            *   
67                                      *           3 or fewer            *   
68                                      *           3 or fewer            *   

   Recent 5-Year Trend‡ in Death Rates(95% Confidence Interval)    State  \
0                                   -1.6 (-1.8, -1.4)            Alabama   
1                                   -1.9 (-2.0, -1.9)            Alabama   
2                                                   *            Alabama   
3                                     0.3 (-1.2, 1.7)            Alabama   
4                                    -0.7 (-2.9, 1.5)            Alabama   
..                                                ...                ...   
64                                                  *            Alabama   
65                                                  *            Alabama   
66                                                  *            Alabama   
67                                                  *            Alabama   
68                                                  *            Alabama   

              Cancer                 Race/Ethnicity        Sex  Age  
0   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50  
1   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50  
2   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50  
3   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50  
4   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50  
..               ...                            ...        ...  ...  
64  All Cancer Sites  All Rac

cancer_num https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=0&age=136&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=0&age=136&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0            Alabama                                  ***   
1      United States                                  ***   
2      Walker County                                  ***   
3     Bullock County                                  ***   
4      Wilcox County                                  ***   
..               ...                                  ...   
64     Greene County                                  ***   
65    Pickens County                                  ***   
66  Limestone County                                  ***   
67    Choctaw County                                  ***   
68     Shelby County                                  ***   

   Age-Adjusted Death Rate†deaths per 100,000(95% Confidence Interval)  \
0                                566.9 (561.9, 572.0)                    
1                                512.0 (511.4, 512.6)                    
2                                719.4 (672.8, 768.3)                    
3                                699.1 (580.7, 834.4)                    
4                                688.1 (580.3, 810.3)                    
..                                                ...                    
64                               498.7 (401.8, 612.4)                    
65                               496.5 (430.1, 570.3)                    
66                               495.9 (461.1, 532.6)                    
67                               492.9 (417.1, 578.7)                    
68                               436.4 (414.0, 459.7)                    

   CI*Rank&fork;(95% Confidence Interval)  Average Annual Count Recent Trend  \
0                                     NaN                  9873      falling   
1                                     NaN                568048      falling   
2                               1 (1, 12)                   183       stable   
3                               2 (1, 58)                    25       stable   
4                               3 (1, 57)                    30       stable   
..                                    ...                   ...          ...   
64                             63 (7, 67)                    19      falling   
65                            64 (18, 67)                    41      falling   
66                            65 (45, 67)                   156      falling   
67                            66 (18, 67)                    30      falling   
68                            67 (63, 67)                   296      falling   

   Recent 5-Year Trend‡ in Death Rates(95% Confidence Interval)    State  \
0                                   -1.7 (-1.9, -1.5)            Alabama   
1                                   -2.1 (-2.4, -1.8)            Alabama   
2                                    -0.2 (-0.5, 0.2)            Alabama   
3                                    -0.1 (-1.0, 0.8)            Alabama   
4                                     0.2 (-0.7, 1.0)            Alabama   
..                                                ...                ...   
64                                  -1.4 (-2.4, -0.4)            Alabama   
65                                  -3.0 (-4.7, -1.4)            Alabama   
66                                  -2.4 (-3.3, -1.4)            Alabama   
67                                  -1.9 (-2.6, -1.1)            Alabama   
68                                  -1.5 (-1.9, -1.0)            Alabama   

              Cancer                 Race/Ethnicity        Sex  Age  
0   All Cancer Sites  All Races (includes Hispanic)  All Sexes  50+  
1   All Cancer Sites  All Races (includes Hispanic)  All Sexes  50+  
2   All Cancer Sites  All Races (includes Hispanic)  All Sexes  50+  
3   All Cancer Sites  All Races (includes Hispanic)  All Sexes  50+  
4   All Cancer Sites  All Races (includes Hispanic)  All Sexes  50+  
..               ...                            ...        ...  ...  
64  All Cancer Sites  All Ra

cancer_num https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=0&age=006&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=0&age=006&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results


...

County Met Healthy People Objective of ***?  \
0              Wyoming                                  ***   
1        United States                                  ***   
2   Hot Springs County                                  ***   
3      Campbell County                                  ***   
4        Goshen County                                  ***   
5    Sweetwater County                                  ***   
6         Crook County                                  ***   
7        Weston County                                  ***   
8      Sheridan County                                  ***   
9       Johnson County                                  ***   
10     Washakie County                                  ***   
11      Fremont County                                  ***   
12      Laramie County                                  ***   
13        Uinta County                                  ***   
14       Platte County                                  ***   
15     Big Horn County                                  ***   
16      Natrona County                                  ***   
17     Converse County                                  ***   
18       Carbon County                                  ***   
19         Park County                                  ***   
20     Niobrara County                                  ***   
21      Lincoln County                                  ***   
22       Albany County                                  ***   
23        Teton County                                  ***   
24     Sublette County                                  ***   

   Age-Adjusted Death Rate†deaths per 100,000(95% Confidence Interval)  \
0                                469.6 (455.9, 483.6)                    
1                                512.0 (511.4, 512.6)                    
2                                618.9 (489.4, 773.6)                    
3                                587.1 (514.1, 667.1)                    
4                                570.9 (486.7, 665.5)                    
5                                558.2 (494.3, 627.7)                    
6                                527.0 (416.1, 658.2)                    
7                                516.3 (405.3, 648.3)                    
8                                512.0 (456.5, 572.5)                    
9                                510.6 (415.8, 621.1)                    
10                               510.2 (411.1, 626.3)                    
11                               509.6 (458.8, 564.5)                    
12                               489.2 (455.3, 524.9)                    
13                               484.2 (404.5, 574.7)                    
14                               483.5 (395.3, 585.9)                    
15                               481.1 (398.7, 575.8)                    
16                               479.2 (441.7, 519.1)                    
17                               450.7 (370.3, 543.5)                    
18                               435.7 (357.8, 525.4)                    
19                               397.0 (350.2, 448.3)                    
20                               376.3 (234.1, 577.0)                    
21                               330.2 (269.6, 400.3)                    
22                               313.8 (262.6, 371.9)                    
23                               304.4 (246.0, 372.1)                    
24                               278.2 (206.5, 366.7)                    

   CI*Rank&fork;(95% Confidence Interval)  Average Annual Count Recent Trend  \
0                                     NaN                   929      falling   
1                                     NaN                568048      falling   
2                               1 (1, 16)                    16      falling   
3                               2 (1, 12)                    56       stable   
4                               3 (1, 15)           

cancer_num https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=56&areatype=county&cancer=001&race=00&sex=0&age=006&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=56&areatype=county&cancer=001&race=00&sex=0&age=006&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0              Wyoming                                  ***   
1        United States                                  ***   
2   Hot Springs County                                  ***   
3      Converse County                                  ***   
4        Goshen County                                  ***   
5       Fremont County                                  ***   
6    Sweetwater County                                  ***   
7        Carbon County                                  ***   
8         Uinta County                                  ***   
9       Laramie County                                  ***   
10     Big Horn County                                  ***   
11       Weston County                                  ***   
12         Park County                                  ***   
13     Campbell County                                  ***   
14     Sheridan County                                  ***   
15     Washakie County                                  ***   
16      Natrona County                                  ***   
17        Crook County                                  ***   
18       Platte County                                  ***   
19      Johnson County                                  ***   
20      Lincoln County                                  ***   
21       Albany County                                  ***   
22     Sublette County                                  ***   
23        Teton County                                  ***   
24     Niobrara County                                  ***   

   Age-Adjusted Death Rate†deaths per 100,000(95% Confidence Interval)  \
0                                   41.7 (39.4, 44.2)                    
1                                   48.4 (48.3, 48.5)                    
2                                   58.8 (35.8, 97.1)                    
3                                   58.6 (42.7, 79.1)                    
4                                   55.9 (39.7, 77.3)                    
5                                   51.7 (42.1, 62.9)                    
6                                   48.0 (39.5, 58.0)                    
7                                   46.4 (31.8, 65.5)                    
8                                   44.5 (32.6, 59.7)                    
9                                   44.2 (38.5, 50.6)                    
10                                  44.1 (27.9, 66.7)                    
11                                  41.7 (23.9, 69.5)                    
12                                  41.2 (31.0, 53.9)                    
13                                  41.2 (33.4, 50.3)                    
14                                  40.9 (31.4, 52.6)                    
15                                  40.7 (24.8, 65.2)                    
16                                  40.5 (34.5, 47.1)                    
17                                  36.7 (21.2, 61.3)                    
18                                  35.7 (20.6, 59.5)                    
19                                  33.9 (19.4, 57.2)                    
20                                  32.9 (22.8, 46.5)                    
21                                  30.0 (21.4, 41.0)                    
22                                  25.9 (14.2, 44.7)                    
23                                  23.7 (16.0, 34.3)                    
24                                                  *                    

   CI*Rank&fork;(95% Confidence Interval) Average Annual Count Recent Trend  \
0                                     NaN                  273      falling   
1                                     NaN               171025      falling   
2                               1 (1, 20)                    4       stable   
3                               2 (1, 15)                   10       stable   
4                               3 (1, 17)                

cancer_num https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=56&areatype=county&cancer=001&race=00&sex=0&age=157&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/deathrates/index.php?stateFIPS=56&areatype=county&cancer=001&race=00&sex=0&age=157&year=0&type=death&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0              Wyoming                                  ***   
1        United States                                  ***   
2      Campbell County                                  ***   
3   Hot Springs County                                  ***   
4    Sweetwater County                                  ***   
5       Johnson County                                  ***   
6         Crook County                                  ***   
7        Goshen County                                  ***   
8      Sheridan County                                  ***   
9        Weston County                                  ***   
10     Big Horn County                                  ***   
11       Platte County                                  ***   
12     Washakie County                                  ***   
13      Fremont County                                  ***   
14      Laramie County                                  ***   
15      Natrona County                                  ***   
16        Uinta County                                  ***   
17     Niobrara County                                  ***   
18       Carbon County                                  ***   
19         Park County                                  ***   
20     Converse County                                  ***   
21      Lincoln County                                  ***   
22        Teton County                                  ***   
23       Albany County                                  ***   
24     Sublette County                                  ***   

   Age-Adjusted Death Rate†deaths per 100,000(95% Confidence Interval)  \
0                                810.7 (783.6, 838.5)                    
1                                871.8 (870.7, 873.0)                    
2                            1,081.7 (928.6, 1,252.4)                    
3                              992.2 (752.7, 1,283.5)                    
4                              956.5 (827.3, 1,100.0)                    
5                              930.7 (743.9, 1,149.8)                    
6                              926.1 (708.5, 1,189.1)                    
7                              907.6 (757.5, 1,078.7)                    
8                              905.4 (796.9, 1,024.4)                    
9                              900.0 (683.8, 1,162.4)                    
10                             876.3 (713.9, 1,064.4)                    
11                             864.4 (693.4, 1,064.6)                    
12                             861.3 (673.9, 1,084.7)                    
13                               856.8 (758.7, 964.0)                    
14                               840.0 (773.5, 910.7)                    
15                               830.8 (756.3, 910.6)                    
16                             817.9 (660.1, 1,001.9)                    
17                             763.2 (462.9, 1,185.6)                    
18                               739.6 (588.9, 916.8)                    
19                               692.9 (602.5, 793.1)                    
20                               679.1 (529.2, 858.2)                    
21                               565.8 (445.0, 708.8)                    
22                               555.7 (436.2, 697.1)                    
23                               549.5 (448.0, 666.9)                    
24                               469.6 (330.8, 647.1)                    

   CI*Rank&fork;(95% Confidence Interval)  Average Annual Count Recent Trend  \
0                                     NaN                   698      falling   
1                                     NaN                427355      falling   
2                               1 (1, 10)                    39       stable   
3                               2 (1, 19)                    12       stable   
4                               3 (1, 16)           

In [12]:
age_mort_df = pd.concat(age_mort_list)
age_mort_df

County Met Healthy People Objective of ***?  \
0           Alabama                                  ***   
1     United States                                  ***   
2    Marengo County                                  ***   
3    Jackson County                                  ***   
4   Randolph County                                  ***   
..              ...                                  ...   
20  Converse County                                  ***   
21   Lincoln County                                  ***   
22     Teton County                                  ***   
23    Albany County                                  ***   
24  Sublette County                                  ***   

   Age-Adjusted Death Rate†deaths per 100,000(95% Confidence Interval)  \
0                                   18.4 (17.7, 19.1)                    
1                                   15.1 (15.1, 15.2)                    
2                                   38.8 (24.2, 58.8)                    
3                                   30.2 (22.0, 40.3)                    
4                                   27.6 (16.0, 44.2)                    
..                                                ...                    
20                               679.1 (529.2, 858.2)                    
21                               565.8 (445.0, 708.8)                    
22                               555.7 (436.2, 697.1)                    
23                               549.5 (448.0, 666.9)                    
24                               469.6 (330.8, 647.1)                    

   CI*Rank&fork;(95% Confidence Interval) Average Annual Count Recent Trend  \
0                                     NaN                  543      falling   
1                                     NaN                30333      falling   
2                               1 (1, 30)                    4            *   
3                               2 (1, 28)                    9       stable   
4                               3 (1, 41)                    3       stable   
..                                    ...                  ...          ...   
20                             19 (7, 23)                   14      falling   
21                            20 (15, 23)                   16      falling   
22                            21 (16, 23)                   15       stable   
23                            22 (17, 23)                   21      falling   
24                            23 (17, 23)                    8      falling   

   Recent 5-Year Trend‡ in Death Rates(95% Confidence Interval)    State  \
0                                   -1.6 (-1.8, -1.4)            Alabama   
1                                   -1.9 (-2.0, -1.9)            Alabama   
2                                                   *            Alabama   
3                                     0.3 (-1.2, 1.7)            Alabama   
4                                    -0.7 (-2.9, 1.5)            Alabama   
..                                                ...                ...   
20                                  -2.1 (-3.4, -0.7)            Wyoming   
21                                  -1.3 (-2.6, -0.1)            Wyoming   
22                                 14.1 (-12.7, 49.2)            Wyoming   
23                                  -4.5 (-5.9, -3.1)            Wyoming   
24                                  -4.1 (-5.6, -2.7)            Wyoming   

              Cancer                 Race/Ethnicity        Sex  Age  \
0   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50   
1   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50   
2   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50   
3   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50   
4   All Cancer Sites  All Races (includes Hispanic)  All Sexes  <50   
..               ...                            ...        ...  ...   
20  All Cancer Sites  All Races (includes Hi

In [14]:
age_mort_df.to_csv('age_mort_unclean.csv', index=False)

In [20]:
age_mort_df1 =age_mort_df.drop("Met Healthy People Objective of ***?", axis='columns')
age_mort_df2 = age_mort_df1.drop("Borough Or Census Area", axis='columns')
age_mort_df3 = age_mort_df2.drop("Parish", axis='columns')
age_mort_df4 = age_mort_df3.dropna()
age_mort_df5 = age_mort_df4.drop("CI*Rank&fork;(95% Confidence Interval)", axis='columns')
age_mort_df5['Age-Adjusted Death Rate cases per 100,000'] = age_mort_df5['Age-Adjusted Death Rate†deaths per 100,000(95% Confidence Interval)'].str.replace(r'\(.*\)', '')
age_mort_df5['Recent 5-Year Trend in Death Rates'] = age_mort_df5['Age-Adjusted Death Rate†deaths per 100,000(95% Confidence Interval)'].str.replace(r'\(.*\)', '')
age_mort_df6 = age_mort_df5.drop(["Age-Adjusted Death Rate†deaths per 100,000(95% Confidence Interval)", 'Recent 5-Year Trend‡ in Death Rates(95% Confidence Interval)'], axis='columns')
age_mort_df7 = age_mort_df6[age_mort_df6['Average Annual Count'] != '3 or fewer']
age_mort_df7 = age_mort_df6[age_mort_df6['Average Annual Count'] != '3 or fewer']
age_mort_df8 = age_mort_df7.drop(['Recent Trend','Recent 5-Year Trend in Death Rates'], axis='columns')
age_mort_df8

C:\Users\drewa\anaconda3\envs\PythonData\lib\site-packages\ipykernel_launcher.py:6: FutureWarning: The default value of regex will change from True to False in a future version.
  
C:\Users\drewa\anaconda3\envs\PythonData\lib\site-packages\ipykernel_launcher.py:7: FutureWarning: The default value of regex will change from True to False in a future version.
  import sys


County Average Annual Count    State            Cancer  \
2      Marengo County                    4  Alabama  All Cancer Sites   
3      Jackson County                    9  Alabama  All Cancer Sites   
4     Randolph County                    3  Alabama  All Cancer Sites   
5       Dallas County                    5  Alabama  All Cancer Sites   
6   Tallapoosa County                    6  Alabama  All Cancer Sites   
..                ...                  ...      ...               ...   
20    Converse County                   14  Wyoming  All Cancer Sites   
21     Lincoln County                   16  Wyoming  All Cancer Sites   
22       Teton County                   15  Wyoming  All Cancer Sites   
23      Albany County                   21  Wyoming  All Cancer Sites   
24    Sublette County                    8  Wyoming  All Cancer Sites   

                   Race/Ethnicity        Sex  Age  \
2   All Races (includes Hispanic)  All Sexes  <50   
3   All Races (includes Hispanic)  All Sexes  <50   
4   All Races (includes Hispanic)  All Sexes  <50   
5   All Races (includes Hispanic)  All Sexes  <50   
6   All Races (includes Hispanic)  All Sexes  <50   
..                            ...        ...  ...   
20  All Races (includes Hispanic)  All Sexes  65+   
21  All Races (includes Hispanic)  All Sexes  65+   
22  All Races (includes Hispanic)  All Sexes  65+   
23  All Races (includes Hispanic)  All Sexes  65+   
24  All Races (includes Hispanic)  All Sexes  65+   

   Age-Adjusted Death Rate cases per 100,000  
2                                      38.8   
3                                      30.2   
4                                      27.6   
5                                      26.0   
6                                      25.7   
..                                       ...  
20                                    679.1   
21                                    565.8   
22                                    555.7   
23                                    549.5   
24                                    469.6   

[10087 rows x 8 columns]

In [22]:
age_mort_df8.to_csv('age_mort.csv', index=False)